# SQL Notebook for SQL Server 2022 data virtualization for delta tables on S3 compatible object storage

This is a SQL notebook to show the data virtualization capabilities in SQL Server 2022 for delta tables on S3 compatible object storage. This notebook is intended for viewing only. However, steps in this notebook can be executed as part of Exercise 5.4 of the SQL Server 2022 workshop at https://aka.ms/sql2022workshop.

# Step 1 - Master Key

Create a master key to protect the database scoped credential. Edit the following statement to put in a strong password

In [7]:
USE [WideWorldImporters]
GO
IF NOT EXISTS (SELECT * FROM sys.symmetric_keys WHERE name = '##MS_DatabaseMasterKey##')
	CREATE MASTER KEY ENCRYPTION BY PASSWORD = '<password>';
GO

Commands completed successfully.

Commands completed successfully.

Total execution time: 00:00:00.057

# Step 2 - Database Scoped Credential

Create a database scoped credential. Edit the following statement to put in the user and password from RootUser and RootPwd from minio

In [9]:
USE [WideWorldImporters];
GO
-- Have to drop the data source first if it exists
IF EXISTS (SELECT * FROM sys.external_data_sources WHERE name = 's3_wwi')
	DROP EXTERNAL DATA SOURCE s3_wwi;
IF EXISTS (SELECT * FROM sys.database_scoped_credentials WHERE name = 's3_wwi_cred')
    DROP DATABASE SCOPED CREDENTIAL s3_wwi_cred;
GO
CREATE DATABASE SCOPED CREDENTIAL s3_wwi_cred
WITH IDENTITY = 'S3 Access Key',
SECRET = '<user>:<password>';
GO

Commands completed successfully.

Commands completed successfully.

Commands completed successfully.

Total execution time: 00:00:00.008

# Step 3 - External Data Source

Create an external data source. Edit the script to put in your local IP address

In [10]:
USE [WideWorldImporters];
GO
IF EXISTS (SELECT * FROM sys.external_data_sources WHERE name = 's3_wwi')
	DROP EXTERNAL DATA SOURCE s3_wwi;
GO
CREATE EXTERNAL DATA SOURCE s3_wwi
WITH
(
 LOCATION = 's3://<local IP>:9000'
,CREDENTIAL = s3_wwi_cred
);
GO

Commands completed successfully.

Commands completed successfully.

Commands completed successfully.

Total execution time: 00:00:00.006

# Step 4 - External file format

Create an external format file for paruqet to be used for external tables

In [11]:
USE [WideWorldImporters];
GO
IF EXISTS (SELECT * FROM sys.external_file_formats WHERE name = 'ParquetFileFormat')
	DROP EXTERNAL FILE FORMAT ParquetFileFormat;
CREATE EXTERNAL FILE FORMAT ParquetFileFormat WITH(FORMAT_TYPE = PARQUET);
GO

Commands completed successfully.

Commands completed successfully.

Total execution time: 00:00:00.009

# Step 5 - Query the delta table

Query the delta table under S3 storage using OPENROWSET()

In [1]:
USE [WideWorldImporters];
GO
SELECT * FROM OPENROWSET
(BULK '/delta/people-10m', 
FORMAT = 'DELTA', DATA_SOURCE = 's3_wwi') as [people];
GO

Commands completed successfully.

(10000000 rows affected)

Displaying Top 5000 rows.

Total execution time: 00:00:59.293

id firstName middleName lastName gender birthDate ssn salary 3770232 Carla Leticia De Angelis F 1966-04-19 05:00:00.0000000 919-13-8946 72390 3770233 Margit Marna Elam F 1985-03-31 05:00:00.0000000 931-39-1662 81855 3770234 Eric Concepcion Parfitt F 1987-05-10 04:00:00.0000000 963-63-6874 60669 3770235 Margarett Lahoma Barwell F 1982-06-08 04:00:00.0000000 903-10-6577 61307 3770236 Kristy Eleanora Zorzetti F 1977-07-13 04:00:00.0000000 940-73-8455 49728 3770237 Monique Angella Dirr F 1974-12-20 05:00:00.0000000 938-96-1038 53678 3770238 Ronni Brittaney O'Moylan F 1980-10-26 04:00:00.0000000 929-24-4471 110457 3770239 Kristie Abbie Posten F 1961-10-23 04:00:00.0000000 901-61-2111 56105 3770240 Cathy Lauretta Slinn F 1992-08-19 04:00:00.0000000 999-64-4074 66045 3770241 Felipa Jacquetta Mapledoram F 1955-07-27 04:00:00.0000000 977-69-7004 81472 3770242 Celestina Milagros Geist F 1998-09-21 04:00:00.0000000 932-75-9764 72075 3770243 Lauren Carmina Wherrit F 1980-11-27 05:00:00.0000000 951-51-5300 109263 3770244 Debora Khalilah Connochie F 1997-06-13 04:00:00.0000000 907-41-6690 92140 3770245 Aida Lynelle Rowntree F 1993-06-30 04:00:00.0000000 666-64-4962 58517 3770246 Renay Zoraida Caulfield F 1964-05-09 04:00:00.0000000 904-37-1780 88412 3770247 Kimberli Lucina Ellsbury F 1967-08-07 04:00:00.0000000 931-41-9078 56275 3770248 Ashlyn Aleta Ingledew F 1970-10-25 04:00:00.0000000 924-41-9871 53929 3770249 Janell Emelina Liddington F 1984-03-23 05:00:00.0000000 944-67-5911 84225 3770250 Teresia Heather Hendrikse F 1959-02-03 05:00:00.0000000 932-79-4399 61076 3770251 Eilene Rosaria Melliard F 1967-04-08 05:00:00.0000000 910-46-7795 49791 3770252 Claudette Carol Vigars F 1965-06-18 04:00:00.0000000 903-62-7431 48170 3770253 Trudie Alva Antonoyev F 1959-05-30 04:00:00.0000000 939-84-6034 86280 3770254 Brynn Deloris Tarplee F 1970-08-20 04:00:00.0000000 959-81-2413 68443 3770255 Carman Drucilla Powys F 1961-11-07 05:00:00.0000000 929-44-2908 82679 3770256 Joycelyn Miranda Bartholomew F 1965-12-07 05:00:00.0000000 920-75-4230 66998 3770257 Asha Coralie Insworth F 1964-07-15 04:00:00.0000000 984-23-3784 73349 3770258 Jocelyn Tanesha Tolworth F 1986-03-21 05:00:00.0000000 994-53-9359 75243 3770259 Bao Ammie Brisland F 1952-11-06 05:00:00.0000000 902-47-1472 76770 3770260 Lorean Heather Eassom F 1980-03-15 05:00:00.0000000 919-51-1782 47139 3770261 Sherly Darcel Camoletto F 1954-02-22 05:00:00.0000000 945-53-5072 59038 3770262 Heike Amee Rodrigues F 1988-03-09 05:00:00.0000000 961-23-4761 51103 3770263 Andera Denae Epsley F 1998-07-19 04:00:00.0000000 971-95-1032 56783 3770264 Natividad Tawana Taynton F 1952-03-26 05:00:00.0000000 969-63-2398 61047 3770265 Bobbi Kristy Ruff F 1961-08-24 04:00:00.0000000 956-59-7552 74413 3770266 Jacalyn Tempie McGrey F 1967-06-07 04:00:00.0000000 989-27-3442 81536 3770267 Aleta Katharine Ghiriardelli F 1965-04-26 04:00:00.0000000 945-18-3725 48552 3770268 Delois Nancy Gaskoin F 1975-06-24 04:00:00.0000000 902-69-2692 90412 3770269 Rona Silva Sicha F 1994-06-10 04:00:00.0000000 931-19-6424 69315 3770270 Elizebeth Latrisha Brownsey F 1996-04-23 04:00:00.0000000 973-32-5374 81344 3770271 Denese Kerrie Richie F 1961-02-01 05:00:00.0000000 924-43-8203 68863 3770272 Raguel Mariko Mattack F 1994-07-15 04:00:00.0000000 939-37-9474 56084 3770273 Candie Jammie Champkins F 1999-09-04 04:00:00.0000000 923-33-9330 95047 3770274 Arlena Katharine Chotty F 1998-11-06 05:00:00.0000000 968-67-1337 37926 3770275 Christi Nannie Upton F 1961-07-26 04:00:00.0000000 911-26-4233 80356 3770276 Jaqueline Clementina Bortolini F 1957-03-10 05:00:00.0000000 951-64-4740 72313 3770277 Sheri Andrea Rutty F 1972-06-25 04:00:00.0000000 958-51-8064 96148 3770278 Nelida Latrina Boorne F 1967-09-16 04:00:00.0000000 973-93-7370 62916 3770279 Loida Sherley Calderonello F 1983-10-01 04:00:00.0000000 937-65-2075 69583 3770280 Billye Slyvia Farney F 1969-08-30 04:00:00.0000000 977-14-3744 28293 3770281 Daina Leonor Maciunas F 1959-02-18 05:00:00.00

# Step 6 - Query delta table with a filter

Query the delta table by using a WHERE clause for a column that is not a partitioned column

In [2]:
USE [WideWorldImporters];
GO
SELECT * FROM OPENROWSET
(BULK '/delta/people-10m', 
FORMAT = 'DELTA', DATA_SOURCE = 's3_wwi') as [people]
WHERE people.ssn = '992-28-8780';
GO

Commands completed successfully.

Use a collation that enables string predicate pushdown and file elimination on storage layer.

(1 row affected)

Total execution time: 00:00:03.568

id firstName middleName lastName gender birthDate ssn salary 3766886 Maryrose Nelly Tolhurst F 1968-03-19 05:00:00.0000000 992-28-8780 65554

# Step 7 - Query delta table with a filter using partitioned column

Query the delta table by using a WHERE clause for a column that is a partiitione column. Note the peformance difference.

In [3]:
USE [WideWorldImporters];
GO
SELECT * FROM OPENROWSET
(BULK '/delta/people-10m', 
FORMAT = 'DELTA', DATA_SOURCE = 's3_wwi') as [people]
WHERE [people].id = 10000000;
GO

Commands completed successfully.

(1 row affected)

Total execution time: 00:00:00.347

id firstName middleName lastName gender birthDate ssn salary 10000000 Joshua Chas Broggio M 1968-07-22 04:00:00.0000000 988-61-6247 85279

# Step 8 - Use CETAS to create parquet files from a delta table

Execute the following T-SQL to create an external table based on parquet files sources from a query from a delta table

In [4]:
USE [WideworldImporters];
GO
IF EXISTS (SELECT * FROM sys.objects WHERE NAME = 'PEOPLE10M_60s')
	DROP EXTERNAL TABLE PEOPLE10M_60s;
GO
CREATE EXTERNAL TABLE PEOPLE10M_60s
WITH 
(   LOCATION = '/delta/1960s',
    DATA_SOURCE = s3_wwi,  
    FILE_FORMAT = ParquetFileFormat)  
AS
SELECT * FROM OPENROWSET
(BULK '/delta/people-10m', FORMAT = 'DELTA', DATA_SOURCE = 's3_wwi') as [people]
WHERE YEAR(people.birthDate) > 1959 AND YEAR(people.birthDate) < 1970;
GO

Commands completed successfully.

Commands completed successfully.

(2080397 rows affected)

Total execution time: 00:00:07.333

# Step 9 - Query new external table based on parquet

A new folder exists as a subset of the original data. Query the new external table

In [5]:
USE [WideWorldImporters];
GO
SELECT * FROM PEOPLE10M_60s
ORDER BY birthDate;
GO

Commands completed successfully.

(2080397 rows affected)

Displaying Top 5000 rows.

Total execution time: 00:00:16.529

id firstName middleName lastName gender birthDate ssn salary 864537 Belkis Marci Galer F 1960-01-08 05:00:00.0000000 973-13-6596 91192 1235984 Daniele Darla Fitter F 1960-01-08 05:00:00.0000000 996-57-5071 48076 9868408 Lynn Kelvin Letterick M 1960-01-08 05:00:00.0000000 943-57-8866 64576 1060672 Yvette Reiko Peye F 1960-01-08 05:00:00.0000000 983-58-4184 68260 9696542 Kimber Halina Fannin F 1960-01-08 05:00:00.0000000 942-89-1684 107463 4963321 Marilu Season Piscopiello F 1960-01-08 05:00:00.0000000 921-85-6976 76928 4362307 Xenia Carolin Caldecutt F 1960-01-08 05:00:00.0000000 980-87-6750 90586 2205786 Simona Rosio Flintiff F 1960-01-08 05:00:00.0000000 950-70-8690 80583 8952371 Lamont August Braim M 1960-01-08 05:00:00.0000000 921-11-9797 88980 4514267 Kaye Ossie Knowlys F 1960-01-08 05:00:00.0000000 931-81-6906 64175 1799397 Krissy Theresa Clayal F 1960-01-08 05:00:00.0000000 910-67-2126 89978 2354539 Madaline Gita Skip F 1960-01-08 05:00:00.0000000 945-53-9823 76474 4951263 Zola Betsey Pryce F 1960-01-08 05:00:00.0000000 909-89-6301 73021 1995701 Kristeen Shila Simione F 1960-01-08 05:00:00.0000000 973-78-9419 33429 1113200 Kathey Mandy Trainer F 1960-01-08 05:00:00.0000000 958-48-7757 85991 9316941 Lawrence Ulysses Caldes M 1960-01-08 05:00:00.0000000 935-37-2123 117106 9985873 Ernest Rueben Manifould M 1960-01-08 05:00:00.0000000 963-48-3689 60415 4684963 Shawnee Paige Meneo F 1960-01-08 05:00:00.0000000 951-48-6150 59127 1228376 Senaida Pamela Flippelli F 1960-01-08 05:00:00.0000000 997-44-4723 108809 4355658 Michaele Kathrin Butler-Bowdon F 1960-01-08 05:00:00.0000000 935-42-3199 26267 252439 Shirley Karrie Colgrave F 1960-01-08 05:00:00.0000000 939-53-3584 68776 9330862 Noel Maxwell Anthoine M 1960-01-08 05:00:00.0000000 915-89-9467 105283 1185569 Sunday Sima Rouf F 1960-01-08 05:00:00.0000000 962-61-7402 36977 1165655 Yvette Roxane Ferriby F 1960-01-08 05:00:00.0000000 973-82-5662 35868 9388460 Tuan Dorsey Weathey M 1960-01-08 05:00:00.0000000 994-38-4031 81075 459679 Dora Chelsea Saleway F 1960-01-08 05:00:00.0000000 920-77-1486 50742 9837350 Son Elliott Handling M 1960-01-08 05:00:00.0000000 940-94-6245 96376 4786095 Roselyn Elouise Anyon F 1960-01-08 05:00:00.0000000 989-11-5672 55439 1432108 Katerine Torri Ambroziak F 1960-01-08 05:00:00.0000000 960-23-2334 53886 2094687 Alverta Majorie Swanwick F 1960-01-08 05:00:00.0000000 931-12-2440 57954 2360811 Fonda Wilhemina Trahar F 1960-01-08 05:00:00.0000000 966-48-3407 67465 1930173 Kelle Ludivina Goodhall F 1960-01-08 05:00:00.0000000 902-94-8936 116828 1568972 Bernardine Jose Lindfors F 1960-01-08 05:00:00.0000000 926-69-6428 33894 284960 Delmy Laticia Bruni F 1960-01-08 05:00:00.0000000 990-69-2604 73405 4513826 Toby Temple Mahomet F 1960-01-08 05:00:00.0000000 929-62-2580 94639 1096774 Deirdre Marvis Chinnery F 1960-01-08 05:00:00.0000000 987-45-3820 37610 350239 Elina Annamarie Attenborrow F 1960-01-08 05:00:00.0000000 911-48-2922 73806 4011733 Karly Valerie De Clairmont F 1960-01-08 05:00:00.0000000 902-92-3909 39159 9159248 Chadwick Gale McCay M 1960-01-08 05:00:00.0000000 992-46-3476 85885 9103749 Roderick Chauncey Brickett M 1960-01-08 05:00:00.0000000 981-94-4862 93561 9720906 Kassie Sheilah Cleator F 1960-01-08 05:00:00.0000000 920-64-2524 67187 204532 Brigitte Cassandra Mallia F 1960-01-08 05:00:00.0000000 907-68-5680 67562 4256792 Sherrill Mattie Courtman F 1960-01-08 05:00:00.0000000 923-22-5781 59533 9986681 Emilio Ernest Fibben M 1960-01-08 05:00:00.0000000 926-73-5570 62947 749157 Elenor Meryl Juzek F 1960-01-08 05:00:00.0000000 969-92-5371 53415 9921041 Leif Tyron Antonsson M 1960-01-08 05:00:00.0000000 923-86-3507 61681 9002336 Carrol Geraldo Ulrik M 1960-01-08 05:00:00.0000000 983-49-5006 35860 2249041 Loreta Debra Plose F 1960-01-08 05:00:00.0000000 918-42-9809 86722 2195816 Kanisha Zelma Abramowitch F 1960-01-08 05:00:00.0000000 962-34-6513 46800 9575194 Emery Cameron Keemar M 1960-01-08 05:00:00.0000000 960-98-2199 71346 954042 Lanell Paulette 